In [18]:
# Python imports
import os
import glob
import numpy as np
import pandas as pd
import geopandas as gpd
import tarfile
from oggm import utils

In [19]:
rgi_reg_df = []
for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    rgi_reg_df.append(gpd.read_file(utils.get_rgi_region_file(rgi_reg, version='70G')))
rgi_reg_df = pd.concat(rgi_reg_df)

In [20]:
df_stats = []
for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    tmp = pd.read_csv(f'RGI70G/b_010/L1/hypsometry/hypsometry_{rgi_reg}_COPDEM30.csv', index_col=0)
    df_stats.append(tmp)
df_stats = pd.concat(df_stats)

In [21]:
assert len(df_stats) == len(rgi_reg_df)

In [22]:
rgi_reg_df = rgi_reg_df.set_index('rgi_id')

In [23]:
rgi_reg_df.loc[~rgi_reg_df.index.isin(df_stats.index)]

Empty GeoDataFrame
Columns: [o1region, o2region, glims_id, anlys_id, subm_id, src_date, cenlon, cenlat, utm_zone, area_km2, primeclass, conn_lvl, surge_type, term_type, glac_name, is_rgi6, termlon, termlat, zmin_m, zmax_m, zmed_m, zmean_m, slope_deg, aspect_deg, aspect_sec, dem_source, lmax_m, geometry]
Index: []

[0 rows x 28 columns]

In [24]:
assert len(df_stats.dropna(how='all')) == len(rgi_reg_df)

In [25]:
rgi_reg_df_all = rgi_reg_df.copy()

In [26]:
min_valid_perc_copdem = 0.99

odir = 'RGI70G/b_010/L1/hypsometry_best_dem/'
utils.mkdir(odir)

chosen_dem = []

for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    min_range = 5
    
    # Ref - RGI
    rgi_reg_df = rgi_reg_df_all.loc[rgi_reg_df_all['o1region'] == rgi_reg]
    
    # Take COPDEM30 for a start
    source = 'COPDEM30'
    hdf = pd.read_csv(f'RGI70G/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (hdf_stats.grid_dx <= 60) & (hdf_stats.valid_dem_perc > 0.90)
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    output_stats = hdf_stats.loc[valid].copy()
    output_hypso = hdf_hypso.loc[valid].copy()
    
    # Continue with COPDEM90
    source = 'COPDEM90'
    hdf = pd.read_csv(f'RGI70G/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.90)
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
    output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
    
    still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]
    print(f'{rgi_reg}: After COPDEM, {len(still_no_good)} left bad.')
    if len(still_no_good) == 0:
        print(f'{rgi_reg}: DONE.')
        pd.concat([output_stats, output_hypso], axis=1).to_csv(odir + f'/hypsometry_{rgi_reg}_best.csv')
        chosen_dem.append(output_stats['dem_source'])
        continue
    
    for rang in [min_range, 1]:
        for source in ['NASADEM', 'RAMP', 'DEM3', 'ASTER', 'TANDEM']:
            
            hdf = pd.read_csv(f'RGI70G/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)
            if 'valid_dem_perc' not in hdf:
                continue

            ids = np.where(hdf.columns.values == 'dem_source')[0][0]
            attr_cols = list(hdf.columns[0:ids+1])
            hypso_cols = list(hdf.columns[ids+1:])

            hdf = hdf.loc[still_no_good.index]

            ids = np.where(hdf.columns.values == 'dem_source')[0][0]
            attr_cols = list(hdf.columns[0:ids+1])
            hypso_cols = list(hdf.columns[ids+1:])

            hdf_stats = hdf[attr_cols].copy()
            hdf_hypso = hdf[hypso_cols]

            valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.99) 
            valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > rang)
            if len(hdf_stats.loc[valid].copy()) == 0:
                continue
            print(f'{rgi_reg}: {source} and minrange {rang} can take over for {len(hdf_stats.loc[valid].copy())}')
            output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
            output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
            still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]

            print(f'{rgi_reg}: After {source} and minrange {rang}, {len(still_no_good)} left bad.')
            if len(still_no_good) == 0:
                print(f'{rgi_reg}: DONE.')
                pd.concat([output_stats, output_hypso], axis=1).to_csv(odir + f'/hypsometry_{rgi_reg}_best.csv')
                chosen_dem.append(output_stats['dem_source'])
                break

01: After COPDEM, 0 left bad.
01: DONE.
02: After COPDEM, 0 left bad.
02: DONE.
03: After COPDEM, 0 left bad.
03: DONE.
04: After COPDEM, 9 left bad.
04: DEM3 and minrange 5 can take over for 5
04: After DEM3 and minrange 5, 4 left bad.
04: ASTER and minrange 5 can take over for 4
04: After ASTER and minrange 5, 0 left bad.
04: DONE.
05: After COPDEM, 0 left bad.
05: DONE.
06: After COPDEM, 0 left bad.
06: DONE.
07: After COPDEM, 0 left bad.
07: DONE.
08: After COPDEM, 0 left bad.
08: DONE.
09: After COPDEM, 0 left bad.
09: DONE.
10: After COPDEM, 0 left bad.
10: DONE.
11: After COPDEM, 0 left bad.
11: DONE.
12: After COPDEM, 0 left bad.
12: DONE.
13: After COPDEM, 0 left bad.
13: DONE.
14: After COPDEM, 0 left bad.
14: DONE.
15: After COPDEM, 0 left bad.
15: DONE.
16: After COPDEM, 0 left bad.
16: DONE.
17: After COPDEM, 0 left bad.
17: DONE.
18: After COPDEM, 0 left bad.
18: DONE.
19: After COPDEM, 118 left bad.
19: RAMP and minrange 5 can take over for 19
19: After RAMP and minrange

In [27]:
chosen_dem = pd.concat(chosen_dem)

In [28]:
assert len(chosen_dem) == len(rgi_reg_df_all)

In [29]:
dem_dict = chosen_dem.to_dict()

In [30]:
import json
with open('chosen_dem_RGI70G_20251029.json', 'w') as f:
    json.dump(dem_dict, f)

In [31]:
chosen_dem.unique()

array(['COPDEM30', 'COPDEM90', 'ASTER', 'DEM3', 'RAMP', 'TANDEM'],
      dtype=object)

In [32]:
chosen_dem.to_csv('chosen_dem_RGI70G_20251029.csv')

In [25]:
still_no_good

o1region o2region        glims_id  anlys_id  subm_id  \
rgi_id                                                                         
RGI2000-v7.0-G-19-00042       19    19-02  G297881E63306S    288807      585   

                                    src_date     cenlon     cenlat  utm_zone  \
rgi_id                                                                         
RGI2000-v7.0-G-19-00042  1957-01-01T00:00:00 -62.110048 -63.305468        20   

                           area_km2  ...    zmin_m    zmax_m     zmed_m  \
rgi_id                               ...                                  
RGI2000-v7.0-G-19-00042  131.241565  ... -8.964561  394.2206  201.10335   

                           zmean_m slope_deg  aspect_deg  aspect_sec  \
rgi_id                                                                 
RGI2000-v7.0-G-19-00042  194.14117    5.4702   136.48387         4.0   

                         dem_source  lmax_m  \
rgi_id                                        
RGI2000-v7.0-G-19-00042    COPDEM90    6716   

                                                                  geometry  
rgi_id                                                                      
RGI2000-v7.0-G-19-00042  POLYGON Z ((-62.01098 -63.27198 0.00000, -62.0...  

[1 rows x 28 columns]

In [31]:
hdf_stats

area_km2  area_grid_km2  valid_dem_perc  grid_dx  \
rgi_id                                                                        
RGI2000-v7.0-G-19-00042  131.241565     130.945900             1.0    170.0   
RGI2000-v7.0-G-19-01879    0.135366       0.135225             1.0     15.0   
RGI2000-v7.0-G-19-01909    0.457315       0.458470             1.0     19.0   
RGI2000-v7.0-G-19-01949    0.019268       0.019440             1.0     12.0   
RGI2000-v7.0-G-19-01951    0.037624       0.037349             1.0     13.0   
RGI2000-v7.0-G-19-01957    0.049210       0.049686             1.0     13.0   
RGI2000-v7.0-G-19-02049    0.088836       0.089180             1.0     14.0   

                            zmin_m     zmax_m     zmed_m    zmean_m  \
rgi_id                                                                
RGI2000-v7.0-G-19-00042  16.000000  17.000000  17.000000  16.864931   
RGI2000-v7.0-G-19-01879   6.556418   8.724484   7.321214   7.323608   
RGI2000-v7.0-G-19-01909  -1.329191   0.388046  -1.045296  -1.021910   
RGI2000-v7.0-G-19-01949  11.216351  13.072499  12.206100  12.200480   
RGI2000-v7.0-G-19-01951  11.902392  13.394264  12.273021  12.273986   
RGI2000-v7.0-G-19-01957  13.397840  15.216348  13.657412  13.925034   
RGI2000-v7.0-G-19-02049  15.200272  18.796045  16.134684  16.408570   

                         terminus_lon  terminus_lat  slope_deg  aspect_deg  \
rgi_id                                                                       
RGI2000-v7.0-G-19-00042    -62.007085    -63.296464   0.007574   78.541245   
RGI2000-v7.0-G-19-01879    -68.706500    -69.109542   0.377332  182.624080   
RGI2000-v7.0-G-19-01909    -74.575165    -70.138911   0.149907   50.013382   
RGI2000-v7.0-G-19-01949    -67.162256    -68.358197   1.045895  198.871490   
RGI2000-v7.0-G-19-01951    -67.164806    -68.352704   0.388983  140.730990   
RGI2000-v7.0-G-19-01957    -67.056754    -68.218823   0.556819  281.966430   
RGI2000-v7.0-G-19-02049    -66.823366    -67.249333   0.872364  114.434814   

                         aspect_sec dem_source  
rgi_id                                          
RGI2000-v7.0-G-19-00042         3.0     TANDEM  
RGI2000-v7.0-G-19-01879         5.0     TANDEM  
RGI2000-v7.0-G-19-01909         2.0     TANDEM  
RGI2000-v7.0-G-19-01949         5.0     TANDEM  
RGI2000-v7.0-G-19-01951         4.0     TANDEM  
RGI2000-v7.0-G-19-01957         7.0     TANDEM  
RGI2000-v7.0-G-19-02049         4.0     TANDEM

In [30]:
output_stats.loc['RGI2000-v7.0-G-19-00042']

KeyError: 'RGI2000-v7.0-G-19-00042'

In [19]:
rgi_reg_df_all.dem_source.unique()

array(['COPDEM30', 'COPDEM90', 'ASTER', 'DEM3', 'RAMP', 'TANDEM'],
      dtype=object)

In [20]:
rgi_reg_df_all.loc[rgi_reg_df_all.dem_source.isin(['ASTER', 'DEM3', 'RAMP', 'TANDEM'])]

o1region o2region        glims_id  anlys_id  subm_id  \
rgi_id                                                                         
RGI2000-v7.0-G-04-00896       04    04-03  G275958E73295N   1018086      817   
RGI2000-v7.0-G-04-00897       04    04-03  G275966E73298N   1018090      817   
RGI2000-v7.0-G-04-01267       04    04-03  G275541E73001N   1018020      817   
RGI2000-v7.0-G-04-01404       04    04-04  G277368E73248N   1018375      817   
RGI2000-v7.0-G-04-03613       04    04-05  G290575E69126N   1022426      817   
...                          ...      ...             ...       ...      ...   
RGI2000-v7.0-G-19-02693       19    19-21  G302645E63794S    289676      585   
RGI2000-v7.0-G-19-02694       19    19-21  G302652E63791S    287795      585   
RGI2000-v7.0-G-19-02695       19    19-21  G302647E63789S    287958      585   
RGI2000-v7.0-G-19-02712       19    19-21  G305281E63435S    288556      585   
RGI2000-v7.0-G-19-02713       19    19-21  G303410E64229S    288018      585   

                                    src_date     cenlon     cenlat  utm_zone  \
rgi_id                                                                         
RGI2000-v7.0-G-04-00896  2001-07-29T00:00:00 -84.041589  73.294664        16   
RGI2000-v7.0-G-04-00897  2001-07-29T00:00:00 -84.034497  73.298235        16   
RGI2000-v7.0-G-04-01267  2001-07-29T00:00:00 -84.458567  73.000620        16   
RGI2000-v7.0-G-04-01404  2001-07-29T00:00:00 -82.632440  73.247955        17   
RGI2000-v7.0-G-04-03613  2002-08-22T00:00:00 -69.425255  69.126126        19   
...                                      ...        ...        ...       ...   
RGI2000-v7.0-G-19-02693  1988-02-29T00:00:00 -57.354376 -63.793904        21   
RGI2000-v7.0-G-19-02694  1988-02-29T00:00:00 -57.347954 -63.790608        21   
RGI2000-v7.0-G-19-02695  1988-02-29T00:00:00 -57.352917 -63.788652        21   
RGI2000-v7.0-G-19-02712  1956-02-01T00:00:00 -54.720919 -63.436136        21   
RGI2000-v7.0-G-19-02713  1988-02-29T00:00:00 -56.589897 -64.229125        21   

                         area_km2  ...       zmin_m     zmax_m     zmed_m  \
rgi_id                             ...                                      
RGI2000-v7.0-G-04-00896  0.010356  ...   549.000000   559.0000   554.0000   
RGI2000-v7.0-G-04-00897  0.032642  ...   531.000000   558.0000   543.0000   
RGI2000-v7.0-G-04-01267  0.011030  ...   535.000000   551.0000   544.0000   
RGI2000-v7.0-G-04-01404  0.075203  ...   766.000000   779.0000   772.0000   
RGI2000-v7.0-G-04-03613  0.013515  ...  1422.000000  1428.0000  1425.0000   
...                           ...  ...          ...        ...        ...   
RGI2000-v7.0-G-19-02693  0.010427  ...   126.000000   167.0000   145.0000   
RGI2000-v7.0-G-19-02694  0.017018  ...    32.000000    48.0000    39.0000   
RGI2000-v7.0-G-19-02695  0.023110  ...    22.000000    39.0000    30.0000   
RGI2000-v7.0-G-19-02712  0.785394  ...    -5.000000   156.0000   110.0000   
RGI2000-v7.0-G-19-02713  0.047745  ...    22.579649    24.5731    23.1223   

                             zmean_m  slope_deg  aspect_deg  aspect_sec  \
rgi_id                                                                    
RGI2000-v7.0-G-04-00896   553.942500   6.966195  130.049710         4.0   
RGI2000-v7.0-G-04-00897   542.852660  11.731244  340.594028         1.0   
RGI2000-v7.0-G-04-01267   543.536870  10.984485  210.754395         6.0   
RGI2000-v7.0-G-04-01404   771.920530   2.009157  204.268112         6.0   
RGI2000-v7.0-G-04-03613  1425.255100   1.458872  350.311213         1.0   
...                              ...        ...         ...         ...   
RGI2000-v7.0-G-19-02693   145.781620  16.781874   35.179367         2.0   
RGI2000-v7.0-G-19-02694    39.008335   6.754133   35.061870         2.0   
RGI2000-v7.0-G-19-02695    29.618750   5.651735   13.513691         1.0   
RGI2000-v7.0-G-19-02712    76.832306  13.595418   85.863980         3.0   
RGI2000-v7.0-G-19-02713    23.188276   0

In [ ]:
# Continue with other range
min_range = 1
for source in ['NASADEM', 'RAMP', 'DEM3', 'ASTER', 'TANDEM']:
    print(f'Still no good: {len(still_no_good)}')
    
    fp = f'output_vardx/hypsometry_rgi{reg}_{source}.csv'
    hdf = pd.read_csv(fp, index_col=0)
    if 'valid_dem_perc' not in hdf:
        continue
        
    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])
        
    hdf = hdf.loc[still_no_good.index]

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.99) 
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    if len(hdf_stats.loc[valid].copy()) == 0:
        continue
    print(f'{source} can take over for {len(hdf_stats.loc[valid].copy())}')
    output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
    output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
    still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]
    if len(still_no_good) == 0:
        break

In [ ]:
still_no_good.anlys_id.values

In [ ]:
import shapely.geometry as shpg
geoms = [shpg.Point(x, y) for x, y in zip(output_stats.terminus_lon, output_stats.terminus_lat)]

In [ ]:
output_stats['geometry'] = geoms

In [ ]:
odf = gpd.GeoDataFrame(output_stats)

In [ ]:
odf.crs = 'EPSG:4326'

In [ ]:
odf.to_file('term_points_rgi01.shp')

In [ ]:
[len(c) for c in odf.columns]

In [ ]:
odf.columns

In [ ]:
odf

In [ ]:
output_stats.index

In [ ]:
rgi_reg_df.index

In [ ]:
still_no_good

In [ ]:
NASADEM -> GIMP -> RAMP -> DEM3 -> ASTER -> TANDEM 

In [ ]:
df_hypso = []
for fp in glob.glob(f'output_vardx/hypsometry_rgi{reg}_*.csv'):
    tmp = pd.read_csv(fp, index_col=0)
    if 'valid_dem_perc' not in tmp:
        continue
    df_hypso.append(tmp)
df_hypso = pd.concat(df_hypso)

In [ ]:
ids = np.where(df_hypso.columns.values == 'dem_source')[0][0]
attr_cols = df_hypso.columns[0:ids+1]
hypso_cols = ['dem_source'] + list(df_hypso.columns[ids+1:])
# attr_cols, hypso_cols

In [ ]:
df_hypso_stats = df_hypso[attr_cols].copy()
df_hypso = df_hypso[hypso_cols]

In [ ]:
reg_hypso = pd.DataFrame()
for source in df_hypso.dem_source.unique():
    tt = df_hypso.loc[df_hypso.dem_source == source].drop('dem_source', axis=1).T
    tt.index = tt.index.astype(int)
    tt = tt.sort_index()
    reg_hypso[source] = tt.loc[-25:].sum(axis=1)

In [ ]:
reg_hypso

In [ ]:
df_hypso[['dem_source', '5975']].dropna()

In [ ]:
df_hypso[['dem_source', '-75']].dropna().dem_source.unique()

In [ ]:
df_hypso[['dem_source', '-25']].dropna().dem_source.unique()

In [ ]:
df_hypso[['dem_source', '-25']].dropna()

In [ ]:
reg_hypso[['ALASKA', 'COPDEM30', 'COPDEM90', 'ASTER']].plot();

In [ ]:
(reg_hypso['COPDEM30'] -  reg_hypso['COPDEM90']).plot();

In [ ]:
pick = df_hypso.loc['RGI2000-v7.0-G-01-06486'].set_index('dem_source', drop=True).T
pick.index = pick.index.astype(int)
pick = pick.sort_index().loc[-25:]
pick.plot();

In [ ]:
df_hypso_stats

In [ ]:
reg_hypso

In [ ]:
df_stats.COPDEM30.unique()

In [ ]:
df.loc[df.COPDEM30.isnull()]

In [ ]:
baaad = df.loc[df.COPDEM30.isnull() & df.COPDEM90.isnull()]

In [ ]:
baaad

In [ ]:
len(baaad)

In [ ]:
baaad.sum()

NASADEM -> GIMP -> RAMP -> DEM3 -> ASTER -> TANDEM 

In [ ]:
len(baaad.loc[(baaad.RAMP != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1) & (baaad.TANDEM != 1)])

In [ ]:
baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1) & (baaad.TANDEM != 1)]

In [ ]:
rgi_reg_df.loc[rgi_reg_df.rgi_id == 'RGI2000-v7.0-G-19-02348']

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
x = np.linspace(0.01, 100, 1000)
plt.plot(x, np.clip(14. * np.sqrt(x) + 10, None, 100));
plt.plot(x, np.clip(8. * np.sqrt(x) + 10, None, 100));

In [ ]:
rgi_reg_df.loc[rgi_reg_df.o1region == '11'].area_km2.max()

In [ ]:
y = d1 * sqrt(a) + d2

In [ ]:
d1 = 14
d2 = 10
y = 50
((y - d2)/d1)**2

In [ ]:
y = 100
((y - d2)/d1)**2

In [ ]:
import pandas as pd

In [ ]:
x = [0.01, 1, 2, 3, 4, 5, 10, 20, 30, 40] + list(range(41, 200))

In [ ]:
tdf = pd.DataFrame(index=x)

In [ ]:
tdf['dx'] = np.clip(d1 * np.sqrt(x) + d2, None, 100)

In [ ]:
tdf['npix'] = tdf.index * 1e6 / tdf['dx']**2

In [ ]:
tdf['npix'].plot();

In [ ]:
import numpy as np
from shapely.geometry import Point, LineString, LinearRing
from shapely.geometry.polygon import Polygon
from geopandas import GeoSeries
import matplotlib.pyplot as plt

x_data = np.array([1, 1, 1.5, 2, 2, 3]) 
y_data = np.array([1, 2, 2, 2, 2.5, 3])
p = [2, 1, 0, 3, 4, 5]

plt.plot(x_data, y_data, 'o');

In [ ]:
LineString(coordinates=np.asarray((x_data, y_data)).T).length

In [ ]:
LineString(coordinates=np.asarray((x_data[p], y_data[p])).T).length

In [ ]:
LinearRing(coordinates=np.asarray((x_data[p], y_data[p])).T)

In [ ]:
np.argmin([1, 1, 2, 3])